# MGT-530 : Group 5 Final Project

- [Scenario 1: Distance Weighted Demand](##Scenario-1-Distance-Weighted-Demand)

In [1]:
pip install ortools

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from ortools.constraint_solver import routing_enums_pb2
from ortools.constraint_solver import pywrapcp
import matplotlib.colors as mcolors


In [4]:
repo_url = 'https://raw.githubusercontent.com/baertsch/MGT-530-SLO/main/'

In [5]:
vehicle_matrix = pd.read_excel(repo_url + 'vhc_matrix_city_excluded.xlsx')
vehicle_matrix = vehicle_matrix.iloc[0:, :1]
vehicle_matrix

Places
0      16
1      91
2      50
3      20
4     127
5     100

In [6]:
v = vehicle_matrix.values.tolist()
v = [item[0] for item in v]

In [ ]:
full_data = pd.read_csv(repo_url + 'data/full_data.csv')

## Code to display the map

In [8]:
npa_coords = full_data[['NPA', 'lat', 'lng']]
depot_row = pd.DataFrame([{'NPA': 0, 'lat': 46.60396069250175, 'lng': 6.538034286509177}])
npa_coords = pd.concat([npa_coords, depot_row], ignore_index=True)
npa_to_coords = npa_coords.set_index('NPA')[['lat', 'lng']].to_dict('index')

In [9]:
def get_color_palette(n):
    palette = sns.color_palette("pastel", n)
    return [mcolors.rgb2hex(color) for color in palette]

def plot_routes_folium(df_results, npa_to_coords):
    depot_coords = npa_to_coords[0]
    m = folium.Map(location=[depot_coords['lat'], depot_coords['lng']], zoom_start=11)
    num_vehicles = df_results[df_results['vehicle_id'] != 'Total'].shape[0]
    colors = get_color_palette(num_vehicles)

    for idx, row in df_results.iterrows():
        if row['vehicle_id'] == 'Total':
            continue
        fg = folium.FeatureGroup(name=f"Vehicle {row['vehicle_id']}")
        route = row['route']
        points = []
        for npa in route:
            try:
                npa_int = int(npa)
            except Exception:
                continue
            coords = npa_to_coords.get(npa_int)
            if coords:
                points.append((coords['lat'], coords['lng']))
        if points:
            folium.PolyLine(
                points,
                color=colors[idx % len(colors)],
                weight=5,
                opacity=1,  # Fully opaque
                popup=f"Vehicle ID: {row['vehicle_id']}"
            ).add_to(fg)
            for lat, lng in points:
                folium.CircleMarker([lat, lng], radius=3, color='black').add_to(fg)
        fg.add_to(m)
    folium.LayerControl(collapsed=False).add_to(m)
    return m

## Scenario 1 Distance Weighted Demand

In [10]:
def create_data_model(subset_distance_matrix, subset_demands, capacities):
    """Stores the data for the problem."""
    data = {}
    # Data multiplied by a factor of 10 to avoid non-integer numbers
    data['distance_matrix'] = subset_distance_matrix
    data['demands'] = subset_demands
    data['vehicle_capacities'] = capacities
    data['num_vehicles'] = len(capacities)
    data['depot'] = 0
    return data


def print_solution(data, manager, routing, solution):
    """Collects solution in a DataFrame for easy CSV export, with NPA in route."""
    results = []
    total_distance = 0
    total_load = 0
    unused_vehicles = []

    for vehicle_id in range(data['num_vehicles']):
        index = routing.Start(vehicle_id)
        route_distance = 0
        route_load = 0
        route = []
        capacity = data['vehicle_capacities'][vehicle_id]

        while not routing.IsEnd(index):
            node_index = manager.IndexToNode(index)
            demand = data['demands'][node_index]
            route_load += demand
            route.append(node_to_npa[node_index])
            previous_index = index
            index = solution.Value(routing.NextVar(index))
            route_distance += routing.GetArcCostForVehicle(previous_index, index, vehicle_id)

        end_node = manager.IndexToNode(index)
        route.append(node_to_npa[end_node])

        if route_load == 0:
            unused_vehicles.append(vehicle_id)
            continue  # Skip empty routes

        results.append({
            "vehicle_id": vehicle_id,
            "capacity": capacity,
            "route": route,
            "distance_km": route_distance ,
            "load": route_load,
        })

        total_distance += route_distance
        total_load += route_load

    # Add summary row
    results.append({
        "vehicle_id": "Total",
        "capacity": "",
        "route": "",
        "distance_km": total_distance,
        "load": total_load,
    })

    df_results = pd.DataFrame(results)
    print(df_results)
    return df_results

### Wednesday

In [11]:
demand_wed_df = pd.read_csv(repo_url + 'data/adjusted_demand_wed.csv', header=None)

demand_wed_df
#### Distance matrix
distance_matrix_wed = pd.read_csv(repo_url + 'data/adjusted_dm_wed.csv',header=None)
distance_matrix_wed = distance_matrix_wed.iloc[1:,1:]
depot_distances = demand_wed_df.iloc[1:,5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_wed = distance_matrix_wed.copy()
distance_matrix_wed.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_wed.loc[-1] = depot_row
distance_matrix_wed.index = distance_matrix_wed.index + 1
distance_matrix_wed = distance_matrix_wed.sort_index()

# Reset column names and index to integers
distance_matrix_wed.columns = range(distance_matrix_wed.shape[1])
distance_matrix_wed.index = range(distance_matrix_wed.shape[0])
dm_wed = distance_matrix_wed.values.tolist()
for i in range(len(dm_wed)):
    dm_wed[i][i] = 0
dm_wed = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_wed]
dm_wed = [[int(round(float(x))) for x in row] for row in dm_wed]

#### Demand matrix 
demand_wed = demand_wed_df.iloc[1:, 4:5]
d_wed = demand_wed.values.tolist()
d_wed = [int(float(item[0])) for item in d_wed]
d_wed = [0] + d_wed
#### Vehicle Matrix
v_wed_full = v * len(dm_wed)
#### CVRP
npa_list = demand_wed_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_wed, subset_demands=d_wed, capacities=v_wed_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)
    return df_results


df_results_wed=main()

    vehicle_id capacity                           route  distance_km   load
0         1138      127              [0, 1055, 1033, 0]           34    127
1         1139      100                    [0, 1304, 0]           10     96
2         1144      127  [0, 1066, 1072, 1073, 1033, 0]           55    127
3         1145      100                    [0, 1304, 0]           10     96
4         1150      127              [0, 1003, 1033, 0]           32    122
..         ...      ...                             ...          ...    ...
121       1417       91              [0, 1035, 1034, 0]           11     85
122       1418       50                    [0, 1305, 0]            6     36
123       1420      127                    [0, 1303, 0]            2     98
124       1421      100                    [0, 1304, 0]           10     96
125      Total                                                  2537  11838

[126 rows x 5 columns]


In [12]:
df_results_wed

vehicle_id capacity                           route  distance_km   load
0         1138      127              [0, 1055, 1033, 0]           34    127
1         1139      100                    [0, 1304, 0]           10     96
2         1144      127  [0, 1066, 1072, 1073, 1033, 0]           55    127
3         1145      100                    [0, 1304, 0]           10     96
4         1150      127              [0, 1003, 1033, 0]           32    122
..         ...      ...                             ...          ...    ...
121       1417       91              [0, 1035, 1034, 0]           11     85
122       1418       50                    [0, 1305, 0]            6     36
123       1420      127                    [0, 1303, 0]            2     98
124       1421      100                    [0, 1304, 0]           10     96
125      Total                                                  2537  11838

[126 rows x 5 columns]

## Thursday

In [13]:
demand_thur_df = pd.read_csv(repo_url + 'data/adjusted_demand_thu.csv',header=None)
#### Distance Matrix
distance_matrix_thur = pd.read_csv(repo_url + 'data/adjusted_dm_thu.csv',header=None)
distance_matrix_thur = distance_matrix_thur.iloc[1:,1:]

depot_distances = demand_thur_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_thur = distance_matrix_thur.copy()
distance_matrix_thur.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_thur.loc[-1] = depot_row
distance_matrix_thur.index = distance_matrix_thur.index + 1
distance_matrix_thur = distance_matrix_thur.sort_index()

# Reset column names and index to integers
distance_matrix_thur.columns = range(distance_matrix_thur.shape[1])
distance_matrix_thur.index = range(distance_matrix_thur.shape[0])
dm_thur = distance_matrix_thur.values.tolist()
for i in range(len(dm_thur)):
    dm_thur[i][i] = 0
dm_thur = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_thur]
dm_thur = [[int(round(float(x))) for x in row] for row in dm_thur]
#### Demand Matrix
demand_thur = demand_thur_df.iloc[1:, 4:5]
d_thur = demand_thur.values.tolist()
d_thur = [int(float(item[0])) for item in d_thur]
d_thur = [0] + d_thur
#### Vehicule Matrix
v_thur_full = v * len(dm_thur)
#### CVRP
npa_list = demand_thur_df.iloc[1:,2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_thur, subset_demands=d_thur, capacities=v_thur_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)
    return df_results

df_results_thu=main()

   vehicle_id capacity                                              route  \
0         983      100                                       [0, 1304, 0]   
1         988      127                                       [0, 1033, 0]   
2         989      100                                       [0, 1304, 0]   
3         994      127  [0, 1116, 1175, 1176, 1174, 1182, 1195, 1166, ...   
4         995      100                                       [0, 1304, 0]   
..        ...      ...                                                ...   
82       1153       91                                       [0, 1036, 0]   
83       1154       50                                       [0, 1031, 0]   
84       1156      127                                       [0, 1303, 0]   
85       1157      100                                       [0, 1304, 0]   
86      Total                                                               

    distance_km  load  
0            10    96  
1            16    92  
2  

## Friday

In [14]:
demand_fri_df = pd.read_csv(repo_url + 'data/adjusted_demand_fri.csv',header=None)
#### Distance Matrix
distance_matrix_fri = pd.read_csv(repo_url + 'data/adjusted_dm_fri.csv',header=None)
distance_matrix_fri = distance_matrix_fri.iloc[1:,1:]
depot_distances = demand_fri_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_fri = distance_matrix_fri.copy()
distance_matrix_fri.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_fri.loc[-1] = depot_row
distance_matrix_fri.index = distance_matrix_fri.index + 1
distance_matrix_fri = distance_matrix_fri.sort_index()

# Reset column names and index to integers
distance_matrix_fri.columns = range(distance_matrix_fri.shape[1])
distance_matrix_fri.index = range(distance_matrix_fri.shape[0])
dm_fri = distance_matrix_fri.values.tolist()
for i in range(len(dm_fri)):
    dm_fri[i][i] = 0
dm_fri = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_fri]
dm_fri = [[int(round(float(x))) for x in row] for row in dm_fri]
#### Demand Matrix
demand_fri = demand_fri_df.iloc[1:, 4:5]
d_fri = demand_fri.values.tolist()
d_fri = [int(float(item[0])) for item in d_fri]
d_fri = [0] + d_fri
#### Vehicule Matrix
v_fri_full = v * len(dm_fri)
#### CVRP
npa_list = demand_fri_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_fri, subset_demands=d_fri, capacities=v_fri_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)

    return df_results

df_results_fri=main()

   vehicle_id capacity                                              route  \
0         779      100                                       [0, 1033, 0]   
1         784      127                                 [0, 1034, 1033, 0]   
2         785      100                                       [0, 1305, 0]   
3         790      127                                       [0, 1305, 0]   
4         791      100                                       [0, 1304, 0]   
..        ...      ...                                                ...   
63        913       91  [0, 1063, 1513, 1059, 1088, 1082, 1081, 1080, ...   
64        914       50                                       [0, 1036, 0]   
65        916      127                           [0, 1117, 1313, 1304, 0]   
66        917      100                                       [0, 1303, 0]   
67      Total                                                               

    distance_km  load  
0            16    92  
1            16   116  
2  

## Saturday

In [15]:
demand_sat_df = pd.read_csv(repo_url + 'data/adjusted_demand_sat.csv',header=None)
#### Distance Matrix
distance_matrix_sat = pd.read_csv(repo_url + 'data/adjusted_dm_sat.csv',header=None)
distance_matrix_sat = distance_matrix_sat.iloc[1:,1:]
depot_distances = demand_sat_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_sat = distance_matrix_sat.copy()
distance_matrix_sat.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_sat.loc[-1] = depot_row
distance_matrix_sat.index = distance_matrix_sat.index + 1
distance_matrix_sat = distance_matrix_sat.sort_index()

# Reset column names and index to integers
distance_matrix_sat.columns = range(distance_matrix_sat.shape[1])
distance_matrix_sat.index = range(distance_matrix_sat.shape[0])
dm_sat = distance_matrix_sat.values.tolist()
for i in range(len(dm_sat)):
    dm_sat[i][i] = 0
dm_sat = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_sat]
dm_sat = [[int(round(float(x))) for x in row] for row in dm_sat]
#### Demand Matrix
demand_sat = demand_sat_df.iloc[1:, 4:5]
d_sat = demand_sat.values.tolist()
d_sat = [int(float(item[0])) for item in d_sat]
d_sat = [0] + d_sat
#### Vehicule Matrix
v_sat_full = v * len(dm_sat)
#### CVRP
npa_list = demand_sat_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_sat, subset_demands=d_sat, capacities=v_sat_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)

    return df_results

df_results_sat=main()

   vehicle_id capacity                                              route  \
0           1       91                           [0, 1143, 1114, 1143, 0]   
1           4      127  [0, 1352, 1354, 1355, 1358, 1439, 1446, 1443, ...   
2         826      127                                 [0, 1054, 1033, 0]   
3         827      100                                       [0, 1304, 0]   
4         832      127                                 [0, 1035, 1033, 0]   
..        ...      ...                                                ...   
72        971      100                                       [0, 1303, 0]   
73        973       91                                       [0, 1305, 0]   
74        976      127                                       [0, 1303, 0]   
75        977      100                                       [0, 1303, 0]   
76      Total                                                               

    distance_km  load  
0            42    87  
1           124   127  
2  

## Scenario 2 Full Demand

### Wednesday

In [16]:
demand_wed_df = pd.read_csv(repo_url + 'data/demand_wed_full.csv', header=None)

demand_wed_df

0              1     2                             3  \
0    index        Commune   NPA  Commune d'annonce / District   
1        0        Penthaz  1303                       Penthaz   
2        0        Penthaz  1303                       Penthaz   
3        0        Penthaz  1303                       Penthaz   
4        1      Penthalaz  1305                     Penthalaz   
..     ...            ...   ...                           ...   
326    232      Chesières  1885                         Ollon   
327    233       Cudrefin  1588                      Cudrefin   
328    234  La Forclaz VD  1866                         Ollon   
329    236      Rougemont  1659                 Château-d'Oex   
330    237          Gryon  1882                         Gryon   

                   4                      5  
0    full_demand_wed  distance_to_venoge_km  
1              100.0                   0.74  
2              100.0                   0.74  
3               46.0                   0.74  
4              100.0                   2.72  
..               ...                    ...  
326              4.0                  69.28  
327             23.0                  69.89  
328              1.0                  72.05  
329              6.0                  74.02  
330              3.0                   77.0  

[331 rows x 6 columns]

#### Distance matrix

In [17]:
distance_matrix_wed = pd.read_csv(repo_url + 'data/dm_mercredi.csv',header=None)
distance_matrix_wed = distance_matrix_wed.iloc[1:,1:]

In [18]:
depot_distances = demand_wed_df.iloc[1:,5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_wed = distance_matrix_wed.copy()
distance_matrix_wed.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_wed.loc[-1] = depot_row
distance_matrix_wed.index = distance_matrix_wed.index + 1
distance_matrix_wed = distance_matrix_wed.sort_index()

# Reset column names and index to integers
distance_matrix_wed.columns = range(distance_matrix_wed.shape[1])
distance_matrix_wed.index = range(distance_matrix_wed.shape[0])

In [19]:
dm_wed = distance_matrix_wed.values.tolist()
for i in range(len(dm_wed)):
    dm_wed[i][i] = 0
dm_wed = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_wed]
dm_wed = [[int(round(float(x))) for x in row] for row in dm_wed]


#### Demand matrix 

In [20]:
demand_wed = demand_wed_df.iloc[1:, 4:5]

In [21]:
d_wed = demand_wed.values.tolist()
d_wed = [int(float(item[0])) for item in d_wed]
d_wed = [0] + d_wed

#### Vehicle Matrix

In [22]:
v_wed_full = v * len(dm_wed)

#### CVRP

In [23]:
npa_list = demand_wed_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

In [24]:

def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_wed, subset_demands=d_wed, capacities=v_wed_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)

    return df_results

df_results_wed2 = main()

    vehicle_id capacity                                              route  \
0            1       91                                       [0, 1306, 0]   
1            4      127                           [0, 1052, 1061, 1041, 0]   
2            7       91                     [0, 1003, 1006, 1081, 1082, 0]   
3         1655      100                                       [0, 1303, 0]   
4         1660      127                           [0, 1585, 1588, 1305, 0]   
..         ...      ...                                                ...   
147       1979      100                                       [0, 1304, 0]   
148       1981       91  [0, 1045, 1409, 1463, 1584, 1587, 1545, 1530, ...   
149       1982       50                                       [0, 1305, 0]   
150       1985      100                                       [0, 1304, 0]   
151      Total                                                               

     distance_km   load  
0              8     74  
1          

### Thursday

In [25]:
demand_thur_df = pd.read_csv(repo_url + 'data/demand_thu_full.csv',header=None)

#### Distance Matrix

In [26]:
distance_matrix_thur = pd.read_csv(repo_url + 'data/dm_jeudi.csv',header=None)
distance_matrix_thur = distance_matrix_thur.iloc[1:,1:]

In [27]:

depot_distances = demand_thur_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_thur = distance_matrix_thur.copy()
distance_matrix_thur.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_thur.loc[-1] = depot_row
distance_matrix_thur.index = distance_matrix_thur.index + 1
distance_matrix_thur = distance_matrix_thur.sort_index()

# Reset column names and index to integers
distance_matrix_thur.columns = range(distance_matrix_thur.shape[1])
distance_matrix_thur.index = range(distance_matrix_thur.shape[0])

In [28]:
dm_thur = distance_matrix_thur.values.tolist()
for i in range(len(dm_thur)):
    dm_thur[i][i] = 0
dm_thur = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_thur]
dm_thur = [[int(round(float(x))) for x in row] for row in dm_thur]

#### Demand Matrix

In [29]:
demand_thur = demand_thur_df.iloc[1:, 4:5]

In [30]:
d_thur = demand_thur.values.tolist()
d_thur = [int(float(item[0])) for item in d_thur]
d_thur = [0] + d_thur

#### Vehicule Matrix

In [31]:
v_thur_full = v * len(dm_thur)

#### CVRP

In [32]:
npa_list = demand_thur_df.iloc[1:,2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

In [33]:
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_thur, subset_demands=d_thur, capacities=v_thur_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)

    return df_results

df_results_thu2=main()

    vehicle_id capacity                           route  distance_km   load
0            4      127        [0, 1116, 1117, 1304, 0]           24    125
1         1462      127  [0, 1885, 1882, 1880, 1006, 0]          160    127
2         1463      100                    [0, 1304, 0]           10    100
3         1468      127        [0, 1446, 1450, 1305, 0]           83    127
4         1469      100                    [0, 1304, 0]           10    100
..         ...      ...                             ...          ...    ...
109       1664       50                    [0, 1031, 0]            8     42
110       1665       20                    [0, 1125, 0]           26     19
111       1666      127              [0, 1304, 1123, 0]           17    125
112       1667      100                    [0, 1304, 0]           10    100
113      Total                                                  6140  10467

[114 rows x 5 columns]


### Friday

In [34]:
demand_fri_df = pd.read_csv(repo_url + 'data/demand_fri_full.csv',header=None)

#### Distance Matrix

In [35]:
distance_matrix_fri = pd.read_csv(repo_url + 'data/dm_vendredi.csv',header=None)
distance_matrix_fri = distance_matrix_fri.iloc[1:,1:]

In [36]:
depot_distances = demand_fri_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_fri = distance_matrix_fri.copy()
distance_matrix_fri.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_fri.loc[-1] = depot_row
distance_matrix_fri.index = distance_matrix_fri.index + 1
distance_matrix_fri = distance_matrix_fri.sort_index()

# Reset column names and index to integers
distance_matrix_fri.columns = range(distance_matrix_fri.shape[1])
distance_matrix_fri.index = range(distance_matrix_fri.shape[0])

In [37]:
dm_fri = distance_matrix_fri.values.tolist()
for i in range(len(dm_fri)):
    dm_fri[i][i] = 0
dm_fri = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_fri]
dm_fri = [[int(round(float(x))) for x in row] for row in dm_fri]

#### Demand Matrix

In [38]:
demand_fri = demand_fri_df.iloc[1:, 4:5]

In [39]:
d_fri = demand_fri.values.tolist()
d_fri = [int(float(item[0])) for item in d_fri]
d_fri = [0] + d_fri

#### Vehicule Matrix

In [40]:
v_fri_full = v * len(dm_fri)

#### CVRP

In [41]:
npa_list = demand_fri_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

In [42]:
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_fri, subset_demands=d_fri, capacities=v_fri_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)

    return df_results

df_results_fri2=main()

   vehicle_id capacity                                              route  \
0           1       91                                 [0, 1003, 1006, 0]   
1           7       91         [0, 1041, 1514, 1526, 1464, 1413, 1374, 0]   
2        1295      100                                       [0, 1304, 0]   
3        1300      127                                 [0, 1117, 1304, 0]   
4        1301      100                                       [0, 1304, 0]   
..        ...      ...                                                ...   
76       1435       91  [0, 1536, 1584, 1586, 1588, 1545, 1404, 1417, ...   
77       1436       50                                       [0, 1036, 0]   
78       1438      127                           [0, 1033, 1070, 1093, 0]   
79       1439      100                                       [0, 1304, 0]   
80      Total                                                               

    distance_km  load  
0            32    90  
1            84    91  
2  

### Saturday

In [43]:
demand_sat_df = pd.read_csv(repo_url + 'data/demand_sat_full.csv',header=None)

#### Distance Matrix

In [44]:
distance_matrix_sat = pd.read_csv(repo_url + 'data/dm_samedi.csv',header=None)
distance_matrix_sat = distance_matrix_sat.iloc[1:,1:]

In [45]:
depot_distances = demand_sat_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_sat = distance_matrix_sat.copy()
distance_matrix_sat.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_sat.loc[-1] = depot_row
distance_matrix_sat.index = distance_matrix_sat.index + 1
distance_matrix_sat = distance_matrix_sat.sort_index()

# Reset column names and index to integers
distance_matrix_sat.columns = range(distance_matrix_sat.shape[1])
distance_matrix_sat.index = range(distance_matrix_sat.shape[0])

In [46]:
dm_sat = distance_matrix_sat.values.tolist()
for i in range(len(dm_sat)):
    dm_sat[i][i] = 0
dm_sat = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_sat]
dm_sat = [[int(round(float(x))) for x in row] for row in dm_sat]

#### Demand Matrix

In [47]:
demand_sat = demand_sat_df.iloc[1:, 4:5]

In [48]:
d_sat = demand_sat.values.tolist()
d_sat = [int(float(item[0])) for item in d_sat]
d_sat = [0] + d_sat

#### Vehicule Matrix

In [49]:
v_sat_full = v * len(dm_sat)

#### CVRP

In [50]:
npa_list = demand_sat_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

In [51]:
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_sat, subset_demands=d_sat, capacities=v_sat_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)
    
    return df_results

df_results_sat2=main()

   vehicle_id capacity                                             route  \
0           1       91  [0, 1817, 1822, 1804, 1805, 1803, 1071, 1093, 0]   
1           2       50              [0, 1437, 1430, 1421, 1420, 1029, 0]   
2           4      127                          [0, 1304, 1115, 1123, 0]   
3           5      100                                      [0, 1304, 0]   
4           7       91                                [0, 1025, 1033, 0]   
..        ...      ...                                               ...   
89       1489       91                                      [0, 1305, 0]   
90       1490       50                                [0, 1377, 1376, 0]   
91       1492      127                    [0, 1358, 1374, 1307, 1304, 0]   
92       1493      100                                      [0, 1303, 0]   
93      Total                                                              

    distance_km  load  
0            99    91  
1            99    49  
2            21

In [52]:
demand_fri_df = pd.read_csv(repo_url + 'data/demand_fri_full.csv',header=None)

#### Distance Matrix

In [53]:
distance_matrix_fri = pd.read_csv(repo_url + 'data/dm_vendredi.csv',header=None)
distance_matrix_fri = distance_matrix_fri.iloc[1:,1:]

In [54]:
depot_distances = demand_fri_df.iloc[1:, 5:].values.tolist()
depot_distances = [item[0] for item in depot_distances]

# Insert depot as first column
distance_matrix_fri = distance_matrix_fri.copy()
distance_matrix_fri.insert(0, 'Depot', depot_distances)

# Insert depot as first row (must match new number of columns)
depot_row = [0.0] + depot_distances
distance_matrix_fri.loc[-1] = depot_row
distance_matrix_fri.index = distance_matrix_fri.index + 1
distance_matrix_fri = distance_matrix_fri.sort_index()

# Reset column names and index to integers
distance_matrix_fri.columns = range(distance_matrix_fri.shape[1])
distance_matrix_fri.index = range(distance_matrix_fri.shape[0])

In [55]:
dm_fri = distance_matrix_fri.values.tolist()
for i in range(len(dm_fri)):
    dm_fri[i][i] = 0
dm_fri = [[9999 if (isinstance(x, float) and np.isinf(x)) else x for x in row] for row in dm_fri]
dm_fri = [[int(round(float(x))) for x in row] for row in dm_fri]

#### Demand Matrix

In [56]:
demand_fri = demand_fri_df.iloc[1:, 4:5]

In [57]:
d_fri = demand_fri.values.tolist()
d_fri = [int(float(item[0])) for item in d_fri]
d_fri = [0] + d_fri

#### Vehicule Matrix

In [58]:
v_fri_full = v * len(dm_fri)

#### CVRP

In [59]:
npa_list = demand_fri_df.iloc[1:, 2:3].reset_index(drop=True).values.tolist()
npa_list = [int(float(item[0])) for item in npa_list]
node_to_npa = [0] + npa_list  # index 0 is depot

In [60]:
def main():
    """Solve the CVRP problem."""

    # Instantiate the data problem.
    data = create_data_model(subset_distance_matrix= dm_fri, subset_demands=d_fri, capacities=v_fri_full)
    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(len(data['distance_matrix']),
                                           data['num_vehicles'], data['depot'])

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)


    # Create and register a transit callback.
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data['distance_matrix'][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)


    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data['demands'][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(
        demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data['vehicle_capacities'],  # vehicle maximum capacities
        True,  # start cumul to zero
        'Capacity')



    # Complete here
    seach_parameters = pywrapcp.DefaultRoutingSearchParameters()
    seach_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    
    solution = routing.SolveWithParameters(seach_parameters)

    if solution:
        df_results= print_solution(data, manager, routing, solution)
        m = plot_routes_folium(df_results, npa_to_coords)
        display(m)



main()

   vehicle_id capacity                                              route  \
0           1       91                                 [0, 1003, 1006, 0]   
1           7       91         [0, 1041, 1514, 1526, 1464, 1413, 1374, 0]   
2        1295      100                                       [0, 1304, 0]   
3        1300      127                                 [0, 1117, 1304, 0]   
4        1301      100                                       [0, 1304, 0]   
..        ...      ...                                                ...   
76       1435       91  [0, 1536, 1584, 1586, 1588, 1545, 1404, 1417, ...   
77       1436       50                                       [0, 1036, 0]   
78       1438      127                           [0, 1033, 1070, 1093, 0]   
79       1439      100                                       [0, 1304, 0]   
80      Total                                                               

    distance_km  load  
0            32    90  
1            84    91  
2  

## Comparison

In [79]:
kg_CO2_eq_per_km = float(0.351772525877379)

### Wednesday

In [93]:
wed_tickets = full_data[~full_data['wed_tickets'].isna()]
total_CO2_wed_ind_car = sum(wed_tickets['wed_tickets']*wed_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
total_CO2_wed_shared_car = sum((wed_tickets['wed_tickets']/4)*wed_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
print('Total kg CO2 eq on Wednesday if everyone goes to their festical alone in their own car:', total_CO2_wed_ind_car)
print('Total kg CO2 eq on Wednesday if everyone goes to their festical in a shared car (4 people in car):', total_CO2_wed_shared_car)

Total kg CO2 eq on Wednesday if everyone goes to their festical alone in their own car: 58297.29782296359
Total kg CO2 eq on Wednesday if everyone goes to their festical in a shared car (4 people in car): 14574.324455740898


In [108]:
demand_wed_df = pd.read_csv(repo_url + 'data/demand_wed.csv')
demand_wed_df['Unserved Demand'] = demand_wed_df['full_demand_wed']-demand_wed_df['adjusted_demand_wed']
total_CO2_wed_diff = sum(demand_wed_df['Unserved Demand']*demand_wed_df['distance_to_venoge_km']) * kg_CO2_eq_per_km

In [120]:
total_dist_wed_1=df_results_wed[df_results_wed['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_wed_1=total_dist_wed_1*kg_CO2_eq_per_km
total_load_wed_1=df_results_wed[df_results_wed['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Wednesday 1st solution with our buses: ", total_dist_wed_1)
print('Total kg CO2 eq for Wednesday by people going on their own: ', total_CO2_wed_diff)
print('Total kg CO2 eq for Wednesday 1st solution: ', total_CO2_wed_1+total_CO2_wed_diff)
print('Total kg CO2 eq for Wednesday 1st solution: ', total_CO2_wed_1)
print("Total load for Wednesday 1st solution served by our buses: ", total_load_wed_1,'\n')
total_dist_wed_2=df_results_wed2[df_results_wed2['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_wed_2=total_dist_wed_2*kg_CO2_eq_per_km
total_load_wed_2=df_results_wed2[df_results_wed2['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Wednesday 2nd solution: ", total_dist_wed_2)
print('Total kg CO2 eq for Wednesday 2nd solution: ', total_CO2_wed_2)
print("Total load for Wednesday 2nd solution: ", total_load_wed_2)

Total distance for Wednesday 1st solution with our buses:  2537
Total kg CO2 eq for Wednesday by people going on their own:  30875.46858148655
Total kg CO2 eq for Wednesday 1st solution:  31767.91547963746
Total kg CO2 eq for Wednesday 1st solution:  892.4468981509106
Total load for Wednesday 1st solution served by our buses:  11838 

Total distance for Wednesday 2nd solution:  6507
Total kg CO2 eq for Wednesday 2nd solution:  2288.983825884105
Total load for Wednesday 2nd solution:  14814


### Thursday

In [94]:
thu_tickets = full_data[~full_data['thu_tickets'].isna()]
total_CO2_thu_ind_car = sum(thu_tickets['thu_tickets']*thu_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
total_CO2_thu_shared_car = sum((thu_tickets['thu_tickets']/4)*thu_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
print('Total kg CO2 eq on Thursday if everyone goes to their festical alone in their own car:', total_CO2_thu_ind_car)
print('Total kg CO2 eq on Thursday if everyone goes to their festical in a shared car (4 people in car):', total_CO2_thu_shared_car)

Total kg CO2 eq on Thursday if everyone goes to their festical alone in their own car: 46675.62707019076
Total kg CO2 eq on Thursday if everyone goes to their festical in a shared car (4 people in car): 11668.90676754769


In [111]:
demand_thur_df = pd.read_csv(repo_url + 'data/demand_thu.csv')
demand_thur_df['Unserved Demand'] = demand_thur_df['full_demand_thu']-demand_thur_df['adjusted_demand_thu']
total_CO2_thur_diff = sum(demand_thur_df['Unserved Demand']*demand_thur_df['distance_to_venoge_km']) * kg_CO2_eq_per_km

In [121]:
total_dist_thu_1=df_results_thu[df_results_thu['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_thu_1=total_dist_thu_1*kg_CO2_eq_per_km
total_load_thu_1=df_results_thu[df_results_thu['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Thursday 1st solution by our buses: ", total_dist_thu_1)
print('Total kg CO2 eq for Thursday 1st solution with our buses: ', total_CO2_thu_1)
print("Total kg CO2 eq for Thursday by people going on their own: ", total_CO2_thur_diff)
print('Total kg CO2 eq for Thursday 1st solution: ', total_CO2_thu_1+total_CO2_thur_diff)
print("Total load for Thursday 1st solution served by our buses: ", total_load_thu_1,'\n')
total_dist_thu_2=df_results_thu2[df_results_thu2['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_thu_2=total_dist_thu_2*kg_CO2_eq_per_km
total_load_thu_2=df_results_thu2[df_results_thu2['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Thursday 2nd solution: ", total_dist_thu_2)
print('Total kg CO2 eq for Thursday 2nd solution: ', total_CO2_thu_2)
print("Total load for Thursday 2nd solution: ", total_load_thu_2)

Total distance for Thursday 1st solution by our buses:  1970
Total kg CO2 eq for Thursday 1st solution with our buses:  692.9918759784366
Total kg CO2 eq for Thursday by people going on their own:  26340.336270194417
Total kg CO2 eq for Thursday 1st solution:  27033.328146172855
Total load for Thursday 1st solution served by our buses:  7924 

Total distance for Thursday 2nd solution:  6140
Total kg CO2 eq for Thursday 2nd solution:  2159.883308887107
Total load for Thursday 2nd solution:  10467


### Friday

In [96]:
fri_tickets = full_data[~full_data['fri_tickets'].isna()]
total_CO2_fri_ind_car = sum(fri_tickets['fri_tickets']*fri_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
total_CO2_fri_shared_car = sum((fri_tickets['fri_tickets']/4)*fri_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
print('Total kg CO2 eq on Friday if everyone goes to their festical alone in their own car:', total_CO2_fri_ind_car)
print('Total kg CO2 eq on Friday if everyone goes to their festical in a shared car (4 people in car):', total_CO2_fri_shared_car)

Total kg CO2 eq on Friday if everyone goes to their festical alone in their own car: 28582.193130786745
Total kg CO2 eq on Friday if everyone goes to their festical in a shared car (4 people in car): 7145.548282696686


In [114]:
demand_fri_df = pd.read_csv(repo_url + 'data/demand_fri.csv')
demand_fri_df['Unserved Demand'] = demand_fri_df['full_demand_fri']-demand_fri_df['adjusted_demand_fri']
total_CO2_fri_diff = sum(demand_fri_df['Unserved Demand']*demand_fri_df['distance_to_venoge_km']) * kg_CO2_eq_per_km

In [122]:
total_dist_fri_1=df_results_fri[df_results_fri['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_fri_1=total_dist_fri_1*kg_CO2_eq_per_km
total_load_fri_1=df_results_fri[df_results_fri['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Friday 1st solution by our buses: ", total_dist_fri_1)
print('Total kg CO2 eq for Friday 1st solution from our buses: ', total_CO2_fri_1)
print("Total kg CO2 eq for Friday by people going on their own: ", total_CO2_fri_diff)
print('Total kg CO2 eq for Friday 1st solution: ', total_CO2_fri_1+total_CO2_fri_diff)
print("Total load for Friday 1st solution served by our buses: ", total_load_fri_1,'\n')
total_dist_fri_2=df_results_fri2[df_results_fri2['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_fri_2=total_dist_fri_2*kg_CO2_eq_per_km
total_load_fri_2=df_results_fri2[df_results_fri2['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Friday 2nd solution: ", total_dist_fri_2)
print('Total kg CO2 eq for Friday 2nd solution: ', total_CO2_fri_2) 
print("Total load for Friday 2nd solution: ", total_load_fri_2)

Total distance for Friday 1st solution by our buses:  1453
Total kg CO2 eq for Friday 1st solution from our buses:  511.1254800998317
Total kg CO2 eq for Friday by people going on their own:  13919.448891803911
Total kg CO2 eq for Friday 1st solution:  14430.574371903744
Total load for Friday 1st solution served by our buses:  6149 

Total distance for Friday 2nd solution:  3811
Total kg CO2 eq for Friday 2nd solution:  1340.6050961186913
Total load for Friday 2nd solution:  7600


### Saturday

In [98]:
sat_tickets = full_data[~full_data['sat_tickets'].isna()]
total_CO2_sat_ind_car = sum(sat_tickets['sat_tickets']*sat_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
total_CO2_sat_shared_car = sum((sat_tickets['sat_tickets']/4)*sat_tickets['distance_to_venoge_km'])*kg_CO2_eq_per_km
print('Total kg CO2 eq on Saturday if everyone goes to their festical alone in their own car:', total_CO2_sat_ind_car)
print('Total kg CO2 eq on Saturday if everyone goes to their festical in a shared car (4 people in car):', total_CO2_sat_shared_car)

Total kg CO2 eq on Saturday if everyone goes to their festical alone in their own car: 36469.20402580245
Total kg CO2 eq on Saturday if everyone goes to their festical in a shared car (4 people in car): 9117.301006450612


In [116]:
demand_sat_df = pd.read_csv(repo_url + 'data/demand_sat.csv')
demand_sat_df['Unserved Demand'] = demand_sat_df['full_demand_sat']-demand_sat_df['adjusted_demand_sat']
total_CO2_sat_diff = sum(demand_sat_df['Unserved Demand']*demand_sat_df['distance_to_venoge_km']) * kg_CO2_eq_per_km

In [118]:
total_dist_sat_1=df_results_sat[df_results_sat['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_sat_1=total_dist_sat_1*kg_CO2_eq_per_km
total_load_sat_1=df_results_sat[df_results_sat['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Saturday 1st solution by our buses: ", total_dist_sat_1)
print('Total kg CO2 eq for Saturday 1st solution from our buses: ', total_CO2_sat_1)
print("Total kg CO2 eq for Saturday by people going on their own: ", total_CO2_sat_diff)
print('Total kg CO2 eq for Saturday 1st solution: ', total_CO2_sat_1+total_CO2_sat_diff)
print("Total load for Saturday 1st solution served by our buses: ", total_load_sat_1,'\n')
total_dist_sat_2=df_results_sat2[df_results_sat2['vehicle_id']=='Total']['distance_km'].values[0]
total_CO2_sat_2=total_dist_sat_2*kg_CO2_eq_per_km
total_load_sat_2=df_results_sat2[df_results_sat2['vehicle_id']=='Total']['load'].values[0]
print("Total distance for Saturday 2nd solution: ", total_dist_sat_2)
print('Total kg CO2 eq for Saturday 2nd solution: ', total_CO2_sat_2)
print("Total load for Saturday 2nd solution: ", total_load_sat_2)

Total distance for Saturday 1st solution by our buses:  1697
Total kg CO2 eq for Saturday 1st solution from our buses:  596.9579764139122
Total kg CO2 eq for Saturday by people going on their own:  18183.49825920441
Total kg CO2 eq for Saturday 1st solution:  18780.456235618323
Total load for Saturday 1st solution served by our buses:  7162 

Total distance for Saturday 2nd solution:  4485
Total kg CO2 eq for Saturday 2nd solution:  1577.699778560045
Total load for Saturday 2nd solution:  9075
